In [1]:
import folium
import pandas as pd
import geojson
import geopandas
import branca
import geojson
from urllib.request import urlopen
from folium.features import GeoJsonPopup, GeoJsonTooltip

with open("multnomah_co_precinct_splits_dist_info_2-2016.zip.geojson") as f:
    counties = geojson.load(f)

results = pd.read_excel("finalresults.xls")

In [ ]:
counties.prec_name

In [2]:
counties = geopandas.GeoDataFrame.from_features(counties, crs="EPSG:4326")

In [3]:
#counties['geometry'][5] + counties['geometry'][6]#counties['FIRST_PREC'] =="2701"]
counties["FIRST_PREC"] = counties["FIRST_PREC"].astype(str).astype(int)

In [4]:
m = folium.Map(location=[45.4962, -122.4772], zoom_start=10)

In [ ]:
# g = folium.GeoJson(
#     counties

    
    
# ).add_to(m)

In [5]:
resultsmerge = counties.merge(results, how="right", left_on ="FIRST_PREC", right_on="Precinct")

In [ ]:
resultsmerge.tail(3)

In [6]:
resultsmerge['FIRST_PREC'] = resultsmerge['FIRST_PREC'].astype(str)

In [7]:
colormap = branca.colormap.LinearColormap(
    vmin=resultsmerge["BidenPercentage"].quantile(0.0),
    vmax=resultsmerge["BidenPercentage"].quantile(1),
    colors=["darkred", "red",  "blue", "darkblue"],
    caption="Precinct level Biden vote share",
)

In [8]:
popup = GeoJsonPopup(
    fields=["FIRST_PREC" , "FIRST_SPLI", "Trump", "Biden",'Jorgensen',
            'Hawkins','Hunter','WriteIn', 'Total', 'BidenPercentage'],
    aliases=['Precinct Name: ', 'Precinct Subdivision: ', 'Donald Trump/Mike Pence: ', 'Joe Biden/Kamala Harris:',
            'Jo Jorgensen / Jeremy (Spike) Cohen:','Howie Hawkins / Angela Walker:',
             'Dario Hunter / Dawn Neptune Adams:','Write In Votes:', 'Total Votes:', 'Joe Biden Vote Percentage:'],
    localize=True,
    labels=True,
    style="background-color: yellow;",
)

In [9]:
tooltip = GeoJsonTooltip(
    fields=["FIRST_PREC" , "FIRST_SPLI", "Trump", "Biden",'Jorgensen',
            'Hawkins','Hunter','WriteIn', 'Total', 'BidenPercentage'],
    aliases=['Precinct Name: ', 'Precinct Subdivision: ', 'Donald Trump/Mike Pence: ', 'Joe Biden/Kamala Harris:',
            'Jo Jorgensen / Jeremy (Spike) Cohen:','Howie Hawkins / Angela Walker:',
             'Dario Hunter / Dawn Neptune Adams:','Write In Votes:', 'Total Votes:', 'Joe Biden Vote Percentage:'],
    localize=True,
    sticky=False,
    labels=True,
    style="""
        background-color: #F0EFEF;
        border: 2px solid black;
        border-radius: 3px;
        box-shadow: 3px;
    """,
    max_width=800,
)

In [10]:
g = folium.GeoJson(
    resultsmerge,
    style_function=lambda x: {
        "fillColor": colormap(x["properties"]["BidenPercentage"])
        if x["properties"]["BidenPercentage"] is not None
        else "transparent",
        "color": "black",
        "fillOpacity": 0.6,
    },
    
    tooltip=tooltip,
    popup=popup,
).add_to(m)
colormap.add_to(m)


In [11]:
m